In [2]:
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)
import random
import numpy as np
import matplotlib.pyplot as plt
from importlib import reload
import subprocess

import mido
import IPython.display as ipd
import pretty_midi
from visual_midi import Plotter
from visual_midi import Preset

import twelve_tone_gen, any_tone_gen
import scales

In [34]:
warnings.filterwarnings("ignore", category=DeprecationWarning)
import twelve_tone_gen
reload(twelve_tone_gen)

song_name = '12_tone_test'
# generate random prime row
prime_row = random.sample(range(0, 12), 12)
# prime_row = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
tt = twelve_tone_gen.TwelveTone(prime_row)

tpb = 480  # ticks per beat
mid = mido.MidiFile(ticks_per_beat=tpb)

tempo = mido.bpm2tempo(120) # tempo beats per minute
# Create a separate track (track 0) for tempo changes
tempo_track = mido.MidiTrack()
mid.tracks.append(tempo_track)
tempo_track.append(mido.MetaMessage('set_tempo', tempo=tempo))

track_list = ['low', 'mid']
no_highs = 12
highs = [f'high_{i}' for i in range(1, no_highs+1)]
track_list += highs
comb = {c: {} for c in track_list}
# # Load default weights for chromatic scale
# # Makes it easier to edit weights for each track
# octave_weights = np.repeat(scales_2.chromatic['octave_weights'], len(track_list))
# duration_weights = np.repeat(scales_2.chromatic['duration_weights'], len(track_list))
octave_weights = [[0,0.1,0.5,1,0.5,0.1,0,0,0],
                  [0,0,0.50,1,1,1,0.50,0.25,0.1]]
high_octaves = [[0,0,0.1,0.25,0.5,1,0.50,0.25,0.1]]*no_highs
octave_weights+=high_octaves
duration_weights = [[0,0,0,0,0.25,0.5,1,0.5],
                    [0,0,0.25,0.75,1.25,0.75,0.25,0.1]]
high_durations = [[0.15,0.45,0.9,1.5,0.45,0.3,0.15,0]]*no_highs
duration_weights+=high_durations
sequence_lengths = [4, 8]
high_seq = [1]*no_highs
sequence_lengths+=high_seq
sd = [0.06, 0.24]
high_sd = [0.18]*no_highs
sd+=high_sd
rp = [0.16, 0.32]
high_rp = [0.12]*no_highs
rp+=high_rp

# add octave and duration weights to comb dict
for i,c in enumerate(comb):
    comb[c]['octave_weights'] = octave_weights[i]
    comb[c]['duration_weights'] = duration_weights[i]
    comb[c]["length"] = sequence_lengths[i]
    comb[c]['sd'] = sd[i]
    comb[c]['rp'] = rp[i]

'''use this code to merge high tracks and add random offsets'''
# Create separate track for all highs
high_track = mido.MidiTrack()
mid.tracks.append(high_track)
high_track.name = 'highs_combined'

offset = 0
max_offset = 8

for i, c in enumerate(comb.values()):
    if i < len(track_list) - no_highs:
        track = mido.MidiTrack()
        mid.tracks.append(track)
        track.name = track_list[i]  # assign the track name
    else:
        track = high_track

    notes, midi_notes = tt.generator(octave_weights=c['octave_weights'], duration_weights=c['duration_weights'],
                                     length=c["length"], tpb=tpb,
                                     duration='variable', velocity='variable',
                                     sd=c['sd'], rest_probability=c['rp'])

    if i > len(track_list) - no_highs:  # if not the first high track
        random_offset = random.randint(0, max_offset)  # generate a random offset within a desired range
        offset += random_offset*tpb  # add the duration of the first note and the random offset

    # Add the note events to the MIDI track
    for j, note in enumerate(midi_notes):
        if i > len(track_list) - no_highs and j == 0:  # if it's a high track and the first note
            note.time += offset  # add the offset to the note's time
        track.append(note)

    if i >= len(track_list) - no_highs:  # reset the offset for the next high track
        offset = 0

'''use this code to create separate tracks for each high and compose manually'''
# for i, c in enumerate(comb.values()):
#     track = mido.MidiTrack()
#     mid.tracks.append(track)
#     track.name = track_list[i] # assign the track name
#     notes, midi_notes = tt.generator(octave_weights=c['octave_weights'], duration_weights=c['duration_weights'],
#                                      length=c["length"], tpb=tpb, 
#                                      duration='variable', velocity='variable',
#                                      sd=c['sd'], rest_probability=c['rp'])
#     # Add the note events to the MIDI track
#     for note in midi_notes:
#         track.append(note)

# Write the MIDI file to disk
midi_path = f'test/{song_name}_tracks_{len(comb)}.mid'
mid.save(midi_path)
# Load the MIDI file using pretty_midi
midi_data = pretty_midi.PrettyMIDI(midi_path)
# # Plot the MIDI data
preset = Preset(plot_width=850, plot_height=600)
plotter = Plotter(preset, plot_max_length_bar=16)
plotter.show_notebook(midi_data)
# Synthesize the MIDI file into a waveform
audio_data = midi_data.synthesize(fs=44100)
# Normalize the audio data
audio_data /= np.max(np.abs(audio_data))
# optional - open in GarageBand or DAW of choice
daw = 'GarageBand'
try:
    subprocess.call(['open', '-a', daw, midi_path])
except:
    print(f'Error opening MIDI file in {daw}.')

# Normalize the audio data
audio_data /= np.max(np.abs(audio_data))

# Play the audio data in the Jupyter notebook
ipd.Audio(audio_data, rate=44100)

Loading BokehJS ...

In [25]:
random_offset = random.randint(0, max_offset)
random_offset

1